<a href="https://colab.research.google.com/github/zw2497/Twitter_Stream_Processing/blob/master/Tweets.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
consumer_key = "voHiOtlHtgaHC92ek5NYTABAZ"
consumer_secret = "qHra6hGcG7wWEEgTP0mrysqHquaLaloF2tkHcNJfM1tcskImgj"
access_token = "1114974821434241024-BZrPQPmONxVrb6NUVnVa6QQwBpy1An"
access_token_secret = "lRqIvcWURI351ixfT5QMogFgHNajKAwG2cTVPKeclGNXP"

In [0]:
# 暂时不需要Tweepy了
# import tweepy

# class MyStreamListener(tweepy.StreamListener):

#    def on_status(self, status):
#        print(status.text)

#    def on_error(self, status_code):
#        if status_code == 420:
#            #returning False in on_data disconnects the stream
#            return False

# auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
# auth.set_access_token(access_token, access_token_secret)
# api = tweepy.API(auth)

# myStreamListener = MyStreamListener()
# myStream = tweepy.Stream(auth = api.auth, listener=myStreamListener)
# myStream.filter(languages=['english'])

In [3]:
!pip install pycurl
!pip install oauth2

In [0]:
import time
import pycurl
import json
import oauth2 as oauth

from sys import version_info
if version_info.major != 2:
  import urllib.parse as urllib
else:
  import urllib

In [0]:
API_ENDPOINT_URL = 'https://stream.twitter.com/1.1/statuses/filter.json'
USER_AGENT = 'TwitterStream 1.0' # This can be anything really

In [6]:
# You need to replace these with your own values
OAUTH_KEYS = {'consumer_key': consumer_key,
              'consumer_secret': consumer_secret,
              'access_token_key': access_token,
              'access_token_secret': access_token_secret}
print(OAUTH_KEYS)

{'consumer_key': 'voHiOtlHtgaHC92ek5NYTABAZ', 'consumer_secret': 'qHra6hGcG7wWEEgTP0mrysqHquaLaloF2tkHcNJfM1tcskImgj', 'access_token_key': '1114974821434241024-BZrPQPmONxVrb6NUVnVa6QQwBpy1An', 'access_token_secret': 'lRqIvcWURI351ixfT5QMogFgHNajKAwG2cTVPKeclGNXP'}


In [0]:
POST_PARAMS = {'include_entities': 0,
               'stall_warning': 'true',
               'language': 'en',
               'locations': '-171, 18, -66, 71'}

In [0]:
class TwitterStream:
    def __init__(self, timeout=False):
        self.oauth_token = oauth.Token(key=OAUTH_KEYS['access_token_key'], secret=OAUTH_KEYS['access_token_secret'])
        self.oauth_consumer = oauth.Consumer(key=OAUTH_KEYS['consumer_key'], secret=OAUTH_KEYS['consumer_secret'])
        self.conn = None
        self.buffer = ''
        self.timeout = timeout
        self.setup_connection()

        
    def setup_connection(self):
        """ Create persistant HTTP connection to Streaming API endpoint using cURL.
        """
        if self.conn:
            self.conn.close()
            self.buffer = ''
        self.conn = pycurl.Curl()
        # Restart connection if less than 1 byte/s is received during "timeout" seconds
        if isinstance(self.timeout, int):
            self.conn.setopt(pycurl.LOW_SPEED_LIMIT, 1)
            self.conn.setopt(pycurl.LOW_SPEED_TIME, self.timeout)
        self.conn.setopt(pycurl.URL, API_ENDPOINT_URL)
        self.conn.setopt(pycurl.USERAGENT, USER_AGENT)
        # Using gzip is optional but saves us bandwidth.
        self.conn.setopt(pycurl.ENCODING, 'deflate, gzip')
        self.conn.setopt(pycurl.POST, 1)
        self.conn.setopt(pycurl.POSTFIELDS, urllib.urlencode(POST_PARAMS))
        self.conn.setopt(pycurl.HTTPHEADER, ['Host: stream.twitter.com',
                                             'Authorization: %s' % self.get_oauth_header()])
        # self.handle_tweet is the method that are called when new tweets arrive
        self.conn.setopt(pycurl.WRITEFUNCTION, self.handle_tweet)

        
    def get_oauth_header(self):
        """ Create and return OAuth header.
        """
        params = {'oauth_version': '1.0',
                  'oauth_nonce': oauth.generate_nonce(),
                  'oauth_timestamp': str(int(time.time()))}
       
        req = oauth.Request(method='POST', parameters=params, url='%s?%s' % (API_ENDPOINT_URL,
                                                                             urllib.urlencode(POST_PARAMS)))
        req.sign_request(oauth.SignatureMethod_HMAC_SHA1(), self.oauth_consumer, self.oauth_token)
        
        req = str(req.to_header()['Authorization']).encode('utf-8')
        return req.decode('utf-8')

      
    def start(self):
        """ Start listening to Streaming endpoint.
        Handle exceptions according to Twitter's recommendations.
        """
        backoff_network_error = 0.25
        backoff_http_error = 5
        backoff_rate_limit = 60
        while True:
            self.setup_connection()
            try:
                self.conn.perform()
            except:
                # Network error, use linear back off up to 16 seconds
                print('Network error: %s' % self.conn.errstr())
                print('Waiting %s seconds before trying again' % backoff_network_error)
                time.sleep(backoff_network_error)
                backoff_network_error = min(backoff_network_error + 1, 16)
                continue
            # HTTP Error
            sc = self.conn.getinfo(pycurl.HTTP_CODE)
            if sc == 420:
                # Rate limit, use exponential back off starting with 1 minute and double each attempt
                print('Rate limit, waiting %s seconds' % backoff_rate_limit)
                time.sleep(backoff_rate_limit)
                backoff_rate_limit *= 2
            else:
                # HTTP error, use exponential back off up to 320 seconds
                print('HTTP error %s, %s' % (sc, self.conn.errstr()))
                print('Waiting %s seconds' % backoff_http_error)
                time.sleep(backoff_http_error)
                backoff_http_error = min(backoff_http_error * 2, 320) 

                
    def handle_tweet(self, data):
        """ This method is called when data is received through Streaming endpoint.
        """
        self.buffer += data.decode('utf-8')
        
        if data.endswith(b'\r\n') and self.buffer.strip():
            # complete message received
            
            message = json.loads(self.buffer)
            self.buffer = ''
            msg = ''
            if message.get('limit'):
                print('Rate limiting caused us to miss %s tweets' % (message['limit'].get('track')))
            elif message.get('disconnect'):
                raise Exception('Got disconnect: %s' % message['disconnect'].get('reason'))
            elif message.get('warning'):
                print('Got warning: %s' % message['warning'].get('message'))
            else:
                print(message)
                print()

In [9]:
ts = TwitterStream()
ts.setup_connection()
ts.start()

('created_at', 'Fri Apr 19 21:05:30 +0000 2019')
('id', 1119346306579947521)
('id_str', '1119346306579947521')
('text', 'See a virtual tour of my listing on 8120 N Gray Log Ln #FoxPoint #WI  #realestate https://t.co/UpLgvD5uRo')
('source', '<a href="https://www.circlepix.com/" rel="nofollow">Circlepix</a>')
('truncated', False)
('in_reply_to_status_id', None)
('in_reply_to_status_id_str', None)
('in_reply_to_user_id', None)
('in_reply_to_user_id_str', None)
('in_reply_to_screen_name', None)
('user', {'id': 2874047431, 'id_str': '2874047431', 'name': 'Jay Schmidt Group', 'screen_name': 'JaySchmidtGroup', 'location': 'Whitefish Bay, WI', 'url': 'http://jayschmidtgroup.com', 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 174, 'friends_count': 187, 'listed_count': 45, 'favourites_count': 4, 'statuses_count': 4564, 'created_at': 'Thu Oct 23 20:46:51 +0000 2014', 'utc_offset': None, 'time_zone': None, 'geo_enabled': True, 'lang': 'en

KeyboardInterrupt: ignored

Network error: Failed writing body (0 != 2584)
Waiting 0.25 seconds before trying again
('created_at', 'Fri Apr 19 21:07:04 +0000 2019')
('id', 1119346700999626755)
('id_str', '1119346700999626755')
('text', 'Guess what we are having tonight? That’s right Jello Shots! We will have 4 different flavors. Only $1 each! Until t… https://t.co/Ask8kKIOrs')
('source', '<a href="http://instagram.com" rel="nofollow">Instagram</a>')
('truncated', True)
('in_reply_to_status_id', None)
('in_reply_to_status_id_str', None)
('in_reply_to_user_id', None)
('in_reply_to_user_id_str', None)
('in_reply_to_screen_name', None)
('user', {'id': 3045137957, 'id_str': '3045137957', 'name': "Risto's Place Food & Spirits", 'screen_name': 'Ristos_Place123', 'location': 'Statesville, NC, US, 28677', 'url': 'http://ristosplace.net/', 'description': None, 'translator_type': 'none', 'protected': False, 'verified': False, 'followers_count': 120, 'friends_count': 338, 'listed_count': 0, 'favourites_count': 6, 'statuses_c

KeyboardInterrupt: ignored

Network error: Failed writing body (0 != 9677)
Waiting 1.25 seconds before trying again


KeyboardInterrupt: ignored